**1. Algunos puntos que me parece interesante que puedas llegar a establecer relaciones son: 
FECHA DE RECOGIDA, CENTRO, CONCENTRACIÓN, DOSIS, RAZA, GENÉTICA, FORMAS ANORMALES (todas y las totales), 
MOTILIDAD4, CALIDAD_MOVIMIENTO4, COLONIAS, COLONIAS4 (en cada punto), COD_TRATAMIENTO, COD_VACUNA, edad del 
verraco en la recogida de semen (FECHA_LLEGADA – FECHA EYACULADO en cada recogida), edad del verraco a la 
llegada (FECHA LLEGADA – FECHA_NACTO), supervivencia del verraco en el centro (FECHA_SALIDA – FECHA LLEGADA), 
PROCEDENCIA, CAUSA_BAJA, LINEA_GEN**

# **Modelo Predictivo - Machine Learning:**

**Modelo predivtivo en busca de conocer si un verraco será productivo o no es función a su raza, procedencia, linea genética, centro y dosis reales en cada una de las extracciones realizadas en él**

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

In [2]:
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier

In [3]:
from sklearn.metrics import precision_score, recall_score, f1_score, accuracy_score, roc_curve, roc_auc_score

In [4]:
pd.options.display.max_columns = None
pd.options.display.max_rows = None

df = pd.read_excel('EYACULADOS.xlsx')
verracos = pd.read_excel('VERRACOS.xlsx')

## Estudio inicial de los datos

**Las dos bases de datos a utilizar son la perteneicente al archivo denominado EYACULADOS.xlsx (almacenada en la cariable "df") y Verracos.xlsx (almacenada en la variable "verracos")**

In [5]:
df.head(5)

CODIGO  FECHA_REC  COD_VERRACO  VERRACO CENTRO  ANALIZADOR  RECOLECTOR  \
0  140901 2020-01-03         2095  620ND06    CAL          68          56   
1  140902 2020-01-03         1872  520ND19    CAL          68          55   
2  140903 2020-01-03         2094  620ND05    CAL          68          83   
3  140904 2020-01-03         2086  620ND96    CAL          68          78   
4  140905 2020-01-03         2470  807DP42    CAL          68          83   

   VOLUMEN  CONCENTRACION  MOTILIDAD  CALIDAD_MOVIMIENTO  DOSIS_POTENCIAL  \
0      317             76          9                   7               10   
1      357             61          9                   7                9   
2      511            156          9                   7               36   
3      497            134          9                   8               30   
4      572            116          9                   7               30   

   DOSIS_REAL  DOSIS_A_DILUIR  DILUYENTE  SEMEN_ANADIR  CONCENTRACION_REAL  \
0          10             0.0      513.0           317                2409   
1           9             0.0      390.0           357                2420   
2          36             0.0     2477.0           511                2214   
3          30             0.0     1993.0           497                2220   
4          30             0.0     1918.0           572                2212   

  VALIDO MOTIVO_DESECHO MOTIVO_DIFERENCIA HETEROSPERMIA CODIGO_HETEROSPERMIA  \
0   True             OK                OK          True          N07DDA10101   
1   True             OK                OK          True          N07DDA10101   
2   True             OK                OK          True          N07DDA10101   
3   True             OK                OK          True          N07DDA10101   
4   True             OK                OK          True          N07DPA10101   

   ENVASADAS  DILUIDO  BOLASER_BLANCO  BOLASER_MA  ID_DILUYENTE  ML_DILUYENTE  \
0    98.3125     True         30995.0         0.0        2730.0         513.0   
1     0.0000     True         30995.0         0.0        2730.0         390.0   
2     0.0000     True         30995.0         0.0        2730.0        2477.0   
3     0.0000     True         30995.0         0.0        2730.0        1993.0   
4    82.0000     True         30995.0         0.0        2730.0        1918.0   

      RAZA  DOSIS DILUIDAS  TEMP_DILUYENTE  CONDUCTIVIDAD  
0  DANBRED              10       20.299999           10.6  
1  DANBRED               9       20.299999           10.4  
2  DANBRED              36       20.299999           10.5  
3  DANBRED              30       20.299999           10.6  
4    DUPIC              30       20.400000            9.6

In [6]:
df['AÑO'] = df['FECHA_REC'].dt.year
df['MES'] = df['FECHA_REC'].dt.month
df.head(5)

CODIGO  FECHA_REC  COD_VERRACO  VERRACO CENTRO  ANALIZADOR  RECOLECTOR  \
0  140901 2020-01-03         2095  620ND06    CAL          68          56   
1  140902 2020-01-03         1872  520ND19    CAL          68          55   
2  140903 2020-01-03         2094  620ND05    CAL          68          83   
3  140904 2020-01-03         2086  620ND96    CAL          68          78   
4  140905 2020-01-03         2470  807DP42    CAL          68          83   

   VOLUMEN  CONCENTRACION  MOTILIDAD  CALIDAD_MOVIMIENTO  DOSIS_POTENCIAL  \
0      317             76          9                   7               10   
1      357             61          9                   7                9   
2      511            156          9                   7               36   
3      497            134          9                   8               30   
4      572            116          9                   7               30   

   DOSIS_REAL  DOSIS_A_DILUIR  DILUYENTE  SEMEN_ANADIR  CONCENTRACION_REAL  \
0          10             0.0      513.0           317                2409   
1           9             0.0      390.0           357                2420   
2          36             0.0     2477.0           511                2214   
3          30             0.0     1993.0           497                2220   
4          30             0.0     1918.0           572                2212   

  VALIDO MOTIVO_DESECHO MOTIVO_DIFERENCIA HETEROSPERMIA CODIGO_HETEROSPERMIA  \
0   True             OK                OK          True          N07DDA10101   
1   True             OK                OK          True          N07DDA10101   
2   True             OK                OK          True          N07DDA10101   
3   True             OK                OK          True          N07DDA10101   
4   True             OK                OK          True          N07DPA10101   

   ENVASADAS  DILUIDO  BOLASER_BLANCO  BOLASER_MA  ID_DILUYENTE  ML_DILUYENTE  \
0    98.3125     True         30995.0         0.0        2730.0         513.0   
1     0.0000     True         30995.0         0.0        2730.0         390.0   
2     0.0000     True         30995.0         0.0        2730.0        2477.0   
3     0.0000     True         30995.0         0.0        2730.0        1993.0   
4    82.0000     True         30995.0         0.0        2730.0        1918.0   

      RAZA  DOSIS DILUIDAS  TEMP_DILUYENTE  CONDUCTIVIDAD   AÑO  MES  
0  DANBRED              10       20.299999           10.6  2020    1  
1  DANBRED               9       20.299999           10.4  2020    1  
2  DANBRED              36       20.299999           10.5  2020    1  
3  DANBRED              30       20.299999           10.6  2020    1  
4    DUPIC              30       20.400000            9.6  2020    1

In [7]:
print(df['AÑO'].value_counts())
print(df['MES'].value_counts())

2015    23414
2017    21919
2020    20761
2016    20234
2018    20094
2019    19847
2014    14042
2013    12638
2012      628
2021      122
Name: AÑO, dtype: int64
9     13848
8     13764
10    13711
12    13637
7     13279
6     12834
3     12752
5     12555
4     12553
11    12288
1     11266
2     11212
Name: MES, dtype: int64


In [8]:
df['CENTRO'].value_counts()

CAL      100158
PEÑAS     48924
TOL        4617
Name: CENTRO, dtype: int64

In [9]:
df['RAZA'].value_counts()

0             50148
DANBRED       24808
AND           10479
PIETUPBJJ      7736
PIETUPBNN      6542
PAC            6518
TDDDD          5352
DUPIC          5178
PIETUPB        3967
AGSG           3900
TEEEE          3597
DNA            2050
PIETAXIOM      1990
DURGENES       1761
ADN            1679
TLLLL          1635
TUUUUIBE       1247
TVVVV          1183
DCAXIOM        1085
LDAX           1075
TPPNP          1028
TPPPPTOP        975
BLUEACMC        846
DCADN           699
TDDPP           698
LWAX            631
LDADN           603
TUUUU           506
PIETUPBFR       492
PI ALEM NP      467
TIIII           456
IBERICO         396
TPPPPELI        276
LWACMC          263
TZZZZGGP        263
LWADN           261
MAXSEG          230
TAAAAGGP        228
DURGENMJJ       223
DURGENG         222
ADNREK          221
DURGENM         205
DURGENESM       165
TUUUUEFI        158
TUUUUCAL        149
L65P+           142
TZZZZ           128
PACCAR          100
PIETSERGAL       87
TUUUUGGP         30


In [10]:
verracos.head()

CODIGO  CLASE VERRACO TATUAJE CENTRO FECHA_NACTO FECHA_LLEGADA  \
0     828  TUUUU     406   A4V7Z    CAL         NaT    2008-01-22   
1     829  TUUUU     407   A2V7W    CAL  2007-03-04    2008-03-06   
2     830  TUUUU     408   A8V2P    CAL  2007-12-21    2008-03-06   
3     831  TUUUU     409   S7N8F    CAL  2007-03-06    2008-03-06   
4     832  TUUUU     410   S8N7D    CAL  2007-05-11    2008-03-06   

  FECHA_SALIDA  ACTIVO STRESS PROCEDENCIA            DESTINO CAUSA_BAJA  \
0   2008-09-03   False    NaN         NaN                NaN         29   
1   2008-09-03   False    NaN         NaN                NaN         29   
2   2009-01-08   False    NaN         NaN  CARNICAS CIEZANAS         15   
3   2008-09-03   False    NaN         NaN                NaN         29   
4   2008-12-11   False    NaN         NaN                NaN         29   

  LINEA_GEN INICIO_AMORT  COSTE_AMORT  MESES_AMORT  COD_ANT  \
0       NaN   2008-01-22         2500           18      828   
1       NaN   2008-03-06         2500           18      829   
2       NaN   2008-03-06         2500           18      830   
3       NaN   2008-03-06         2500           18      831   
4       NaN   2008-03-06         2500           18      832   

   PROPIEDAD_CLIENTE COD_CLIENTE ULTIMA_AMORTIZACION  IMP_PTE_AMORTIZAR  \
0              False         NaN                 NaT                NaN   
1              False         NaN                 NaT                NaN   
2              False         NaN                 NaT                NaN   
3              False         NaN                 NaT                NaN   
4              False         NaN                 NaT                NaN   

  NUM_ACTIVO_FIJO  RECLAMADO CUARENTENA GENETICA RAZA2 FECHA_ENTRADA_PROD  
0             NaN      False        NaN      NaN   NaN                NaT  
1             NaN      False        NaN      NaN   NaN                NaT  
2             NaN      False        NaN      NaN   NaN                NaT  
3             NaN      False        NaN      NaN   NaN                NaT  
4             NaN      False        NaN      NaN   NaN                NaT

In [11]:
verracos['LINEA_GEN'].value_counts()

PIETUPB      214
DANBRED      197
PAC          106
TDDDD         70
AND           65
DURGEN        38
DUPIC         35
PTAXIOM       34
TUUUU         34
TEEEE         33
TAAAA         33
TVVVV         28
TZZZZ         27
TPPPP         27
BLUEACMC      21
TLLLL         20
LDAX          18
DNA           18
AGSG          17
TDDPP         16
PTADN         13
DURAXIOM      12
TIIII         12
LWACMC        10
LWAX          10
PTSER          9
TNNNN          8
TPPNP          8
LDADN          8
PTALE          7
DURADN         7
MAXSEG         5
LWADN          5
PIETRAIN       5
L65            4
PIETUPBFR      4
TBBBB          4
ADNREK         4
IBERICO        3
TPPNN          3
PTAUSBAR       1
PIETGEN        1
Name: LINEA_GEN, dtype: int64

In [12]:
verracos['PROCEDENCIA'].value_counts()

PEÑAS DE SAN PEDRO                                    159
MEJORADA                                              102
ANTONIO LOPEZ                                          83
BURUTAIN                                               53
ESCORIAL                                               50
PEÑAS                                                  48
QUALITAT ESPERMATICA                                   44
AIM LEON                                               42
TAFALLA                                                37
SINOVAS                                                34
GANADOS PERALTA S.L                                    24
ACOMPOR                                                24
ALMENAR                                                23
ZAHARA                                                 22
GENESUS INC OAKVILLE MB ID NO 5326121                  18
EXPLOTACIONES CUFA                                     17
CAN JAUMO                                              17
LA COMETA     

**Para saber si un verraco es productivo o no es necesario establecer un mínimo de dosis reales producidas en un año**

In [13]:
# Agrupo por cada verraco y cuento sus dosis reales en sus años de producción. Reseteo los índices con el objetivo de poder hacer un merge con estos
group_1 = df.groupby(['COD_VERRACO', 'AÑO'])['DOSIS_REAL'].count()
group_1 = pd.DataFrame(group_1)
group_1 = group_1.reset_index()
group_1.head()

COD_VERRACO   AÑO  DOSIS_REAL
0          770  2013           1
1         1048  2012           3
2         1048  2013          18
3         1049  2012           3
4         1049  2013          12

In [14]:
group_1.shape

(3146, 3)

In [15]:
merged = pd.merge(df, group_1, on=['COD_VERRACO', 'AÑO'])

In [16]:
merged.head(10)

CODIGO  FECHA_REC  COD_VERRACO  VERRACO CENTRO  ANALIZADOR  RECOLECTOR  \
0  140901 2020-01-03         2095  620ND06    CAL          68          56   
1  141423 2020-01-13         2095  620ND06    CAL          68          55   
2  141683 2020-01-17         2095  620ND06    CAL          68          78   
3  141838 2020-01-20         2095  620ND06    CAL          68          55   
4  142047 2020-01-24         2095  620ND06    CAL          68          83   
5  142252 2020-01-27         2095  620ND06    CAL          68          83   
6  142651 2020-02-03         2095  620ND06    CAL          68          55   
7  142857 2020-02-07         2095  620ND06    CAL          68          55   
8  143016 2020-02-10         2095  620ND06    CAL          68          83   
9  142449 2020-01-29         2095  620ND06    CAL          68          78   

   VOLUMEN  CONCENTRACION  MOTILIDAD  CALIDAD_MOVIMIENTO  DOSIS_POTENCIAL  \
0      317             76          9                   7               10   
1      562             87          8                   7               22   
2      639            166          9                   7               48   
3      272             96          9                   8               11   
4      500             76          9                   8               17   
5      433             92          9                   7               18   
6      643            111          9                   8               32   
7      354             66          9                   7               10   
8      458             72          9                   7               14   
9      380             56          8                   7                9   

   DOSIS_REAL_x  DOSIS_A_DILUIR  DILUYENTE  SEMEN_ANADIR  CONCENTRACION_REAL  \
0            10             0.0      513.0           317                2409   
1            22             0.0     1264.0           562                2222   
2            48             0.0     3345.0           639                2210   
3            11             0.0      641.0           272                2374   
4            17             0.0      911.0           500                2235   
5            18             0.0     1061.0           433                2213   
6            32             0.0     2013.0           643                2230   
7            10             0.0      476.0           354                2336   
8            14             0.0      704.0           458                2355   
9             0             0.0        0.0            32                   0   

  VALIDO MOTIVO_DESECHO MOTIVO_DIFERENCIA HETEROSPERMIA CODIGO_HETEROSPERMIA  \
0   True             OK                OK          True          N07DDA10101   
1   True             OK                OK          True          N07DDA10303   
2   True             OK                OK          True          N07DDA10310   
3   True             OK                OK          True          N07DDA10403   
4   True             OK                OK          True          N07DDA10406   
5   True             OK                OK          True          N07DDA10502   
6   True             OK                OK          True          N07DDA10602   
7   True             OK                OK          True          N07DDA10606   
8   True             OK                OK          True          N07DDA10703   
9  False              F                OK         False                  NaN   

   ENVASADAS  DILUIDO  BOLASER_BLANCO  BOLASER_MA  ID_DILUYENTE  ML_DILUYENTE  \
0    98.3125     True         30995.0         0.0        2730.0         513.0   
1    68.6250     True         31483.0         0.0        2749.0        1264.0   
2     0.0000     True         31475.0         0.0        2760.0        3345.0   
3     0.0000     True         31343.0         0.0        2765.0         641.0   
4     0.0000     True         30832.0         0.0        2774.0         911.0   
5     0.0000     True         30999.0         0.0        27

**DOSIS_REAL_y es el valor de la producción de dosis anual en el año de la fecha de recogida. En base a este dato y suponiendo que, para ser considerado productivo, un verraco ha de producir más de 50 dosis al año, creo la nueva columna 'PRODUCTIVO' con valores 1 si es productivo, 0 si no.**

In [17]:
merged['DOSIS_REAL_y'].unique()

array([ 18,  11,  45,  17,  81,   2,  73,  37,  62,  56,  36,  80,  84,
        70,  86,  58,  65,  28, 120,  44,   9, 128, 101,  51,  64,  61,
        48,  33,  53,  82, 130,  60,  46,  77,  92,  76,  47,  72,  31,
        79,  71,  90,  95,  26,  19, 138,  94, 139, 141, 135, 134, 133,
       126, 147, 131, 136,  30, 123,  24,  40,  21,  29,  27,  39,   4,
        89,   1,  42,  14,  32,  59, 140,  10, 143, 116,  22, 145, 100,
        63,  88,  15,  85,  54,  35,  74,  83,  20,  69,  52,  41,   7,
       109,  99,  50,  55,  13,  23,  49, 121, 103,  87,  43,  75,  34,
        68,  91, 125,  16, 127,  78,   5,  67,  66,  57,  12,  25,   3,
         8,   6, 104,  97, 106,  96, 144, 107, 114, 115, 118, 108, 112,
        98, 166, 119, 105, 132, 102, 113, 152, 165, 156, 111,  93,  38,
       122, 117, 124, 110, 129, 137, 142, 148, 154, 151])

In [18]:
merged['PRODUCTIVO'] = 0

In [19]:
merged['PRODUCTIVO'] = np.where(merged['DOSIS_REAL_y'] >= 80, 1, 0)

In [20]:
merged.head()

CODIGO  FECHA_REC  COD_VERRACO  VERRACO CENTRO  ANALIZADOR  RECOLECTOR  \
0  140901 2020-01-03         2095  620ND06    CAL          68          56   
1  141423 2020-01-13         2095  620ND06    CAL          68          55   
2  141683 2020-01-17         2095  620ND06    CAL          68          78   
3  141838 2020-01-20         2095  620ND06    CAL          68          55   
4  142047 2020-01-24         2095  620ND06    CAL          68          83   

   VOLUMEN  CONCENTRACION  MOTILIDAD  CALIDAD_MOVIMIENTO  DOSIS_POTENCIAL  \
0      317             76          9                   7               10   
1      562             87          8                   7               22   
2      639            166          9                   7               48   
3      272             96          9                   8               11   
4      500             76          9                   8               17   

   DOSIS_REAL_x  DOSIS_A_DILUIR  DILUYENTE  SEMEN_ANADIR  CONCENTRACION_REAL  \
0            10             0.0      513.0           317                2409   
1            22             0.0     1264.0           562                2222   
2            48             0.0     3345.0           639                2210   
3            11             0.0      641.0           272                2374   
4            17             0.0      911.0           500                2235   

  VALIDO MOTIVO_DESECHO MOTIVO_DIFERENCIA HETEROSPERMIA CODIGO_HETEROSPERMIA  \
0   True             OK                OK          True          N07DDA10101   
1   True             OK                OK          True          N07DDA10303   
2   True             OK                OK          True          N07DDA10310   
3   True             OK                OK          True          N07DDA10403   
4   True             OK                OK          True          N07DDA10406   

   ENVASADAS  DILUIDO  BOLASER_BLANCO  BOLASER_MA  ID_DILUYENTE  ML_DILUYENTE  \
0    98.3125     True         30995.0         0.0        2730.0         513.0   
1    68.6250     True         31483.0         0.0        2749.0        1264.0   
2     0.0000     True         31475.0         0.0        2760.0        3345.0   
3     0.0000     True         31343.0         0.0        2765.0         641.0   
4     0.0000     True         30832.0         0.0        2774.0         911.0   

      RAZA  DOSIS DILUIDAS  TEMP_DILUYENTE  CONDUCTIVIDAD   AÑO  MES  \
0  DANBRED              10       20.299999           10.6  2020    1   
1  DANBRED              22       20.500000           10.7  2020    1   
2  DANBRED              48       20.299999           10.4  2020    1   
3  DANBRED              11       20.500000           10.5  2020    1   
4  DANBRED              17       20.200001           10.4  2020    1   

   DOSIS_REAL_y  PRODUCTIVO  
0            18           0  
1            18           0  
2            18           0  
3            18           0  
4            18           0

In [21]:
merged['PRODUCTIVO'].value_counts()

1    78700
0    74999
Name: PRODUCTIVO, dtype: int64

**Del data frame de VERRACOS no nos interesa toda la información existente. Me creo un data frame que posteriormente uniremos a "datos_modelo"**

**Así mismo, del dataframe de EYACULADOS no nos interesa toda la información**

In [22]:
small_verracos = verracos.loc[:, ['LINEA_GEN', 'CODIGO', 'PROCEDENCIA']]
small_eyaculados = merged.loc[:, ['COD_VERRACO', 'CENTRO', 'DOSIS_REAL_x', 'RAZA', 'AÑO', 'DOSIS_REAL_y', 'PRODUCTIVO']]

In [23]:
small_verracos.head(5)

LINEA_GEN  CODIGO PROCEDENCIA
0       NaN     828         NaN
1       NaN     829         NaN
2       NaN     830         NaN
3       NaN     831         NaN
4       NaN     832         NaN

In [24]:
small_eyaculados.head()

COD_VERRACO CENTRO  DOSIS_REAL_x     RAZA   AÑO  DOSIS_REAL_y  PRODUCTIVO
0         2095    CAL            10  DANBRED  2020            18           0
1         2095    CAL            22  DANBRED  2020            18           0
2         2095    CAL            48  DANBRED  2020            18           0
3         2095    CAL            11  DANBRED  2020            18           0
4         2095    CAL            17  DANBRED  2020            18           0

**Hay que ligar la tabla "datos_modelo" junto con "verracos" según el código del verraco para añadir en "datos_modelo" el valor de LIENA_GEN y PROCEDENCIA**

In [25]:
datos_modelo = pd.merge(small_eyaculados, small_verracos, left_on='COD_VERRACO', right_on='CODIGO', how='outer')

In [26]:
datos_modelo.head()

COD_VERRACO CENTRO  DOSIS_REAL_x     RAZA     AÑO  DOSIS_REAL_y  \
0       2095.0    CAL          10.0  DANBRED  2020.0          18.0   
1       2095.0    CAL          22.0  DANBRED  2020.0          18.0   
2       2095.0    CAL          48.0  DANBRED  2020.0          18.0   
3       2095.0    CAL          11.0  DANBRED  2020.0          18.0   
4       2095.0    CAL          17.0  DANBRED  2020.0          18.0   

   PRODUCTIVO LINEA_GEN  CODIGO                        PROCEDENCIA  
0         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE  
1         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE  
2         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE  
3         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE  
4         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE

In [27]:
datos_modelo.shape

(154216, 10)

## PREPROCESAMIENTO - ANÁLISI Y LIMPIEZA

**Una vez seleccionado y calculado los datos necesarios para el correcto funcionamiento del modelo, procedo a hacer la correspondiente limpieza de datos en busca de valores NaN, NaT o valores carentes de sentido**

In [28]:
datos_modelo.shape

(154216, 10)

In [29]:
print(datos_modelo.isnull().sum().sum())

45218


**Existe un total de 45.218 valores NaN, voy a localizar dónde están exactamente:**

In [30]:
datos_modelo.isnull().sum()

COD_VERRACO       517
CENTRO            517
DOSIS_REAL_x      517
RAZA             1091
AÑO               517
DOSIS_REAL_y      517
PRODUCTIVO        517
LINEA_GEN       20952
CODIGO            214
PROCEDENCIA     19859
dtype: int64

**Como tanto en CODIGO como en COD_VERRACO existen valores nulos siendo estos verracos sin código asignado, los elimino directamente. Son verracos a los que no se les puede realizar un seguimiento**

In [31]:
datos_modelo = datos_modelo.dropna(subset=["COD_VERRACO"])
datos_modelo = datos_modelo.dropna(subset=["CODIGO"])

In [32]:
datos_modelo.isnull().sum()

COD_VERRACO         0
CENTRO              0
DOSIS_REAL_x        0
RAZA              574
AÑO                 0
DOSIS_REAL_y        0
PRODUCTIVO          0
LINEA_GEN       20246
CODIGO              0
PROCEDENCIA     19391
dtype: int64

**Al ser variables categóricas (y no poder asignar la media de los valores de los verracos semejantes, por ejemplo) he decidido eliminar los NaN restantes**

In [33]:
datos_modelo = datos_modelo.dropna(subset=["LINEA_GEN"])
datos_modelo = datos_modelo.dropna(subset=["PROCEDENCIA"])
datos_modelo = datos_modelo.dropna(subset=["RAZA"])

In [34]:
datos_modelo.isnull().sum()

COD_VERRACO     0
CENTRO          0
DOSIS_REAL_x    0
RAZA            0
AÑO             0
DOSIS_REAL_y    0
PRODUCTIVO      0
LINEA_GEN       0
CODIGO          0
PROCEDENCIA     0
dtype: int64

In [35]:
print(datos_modelo.shape)
print(datos_modelo.isnull().sum().sum())

(115101, 10)
0


In [36]:
datos_modelo.head()

COD_VERRACO CENTRO  DOSIS_REAL_x     RAZA     AÑO  DOSIS_REAL_y  \
0       2095.0    CAL          10.0  DANBRED  2020.0          18.0   
1       2095.0    CAL          22.0  DANBRED  2020.0          18.0   
2       2095.0    CAL          48.0  DANBRED  2020.0          18.0   
3       2095.0    CAL          11.0  DANBRED  2020.0          18.0   
4       2095.0    CAL          17.0  DANBRED  2020.0          18.0   

   PRODUCTIVO LINEA_GEN  CODIGO                        PROCEDENCIA  
0         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE  
1         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE  
2         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE  
3         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE  
4         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE

**Una vez eliminados los NaN, se analizan particularidades**

In [37]:
datos_modelo['CENTRO'].value_counts()

CAL      75155
PEÑAS    36165
TOL       3781
Name: CENTRO, dtype: int64

**Nada mal en CENTRO**

In [38]:
datos_modelo['RAZA'].value_counts()

0             23941
DANBRED       21051
AND            8513
PIETUPBNN      6542
PIETUPBJJ      6423
PAC            5417
TDDDD          5349
DUPIC          5152
PIETUPB        3967
TEEEE          3595
DNA            2050
PIETAXIOM      1989
DURGENES       1759
AGSG           1725
TLLLL          1635
ADN            1583
TUUUUIBE       1247
TVVVV          1173
DCAXIOM         999
LDAX            989
TPPNP           875
TPPPPTOP        871
BLUEACMC        779
TDDPP           698
LWAX            631
LDADN           548
PIETUPBFR       492
PI ALEM NP      464
TIIII           451
DCADN           428
IBERICO         396
TUUUU           294
TPPPPELI        276
LWADN           261
TZZZZGGP        236
MAXSEG          230
DURGENMJJ       223
DURGENG         222
ADNREK          221
DURGENM         205
TAAAAGGP        199
DURGENESM       165
L65P+           142
LWACMC          127
TUUUUEFI        116
TZZZZ           111
PACCAR          100
PIETSERGAL       87
TUUUUCAL         87
TUUUUGGP         30


**Hay una raza denominada '-' y otra con nombre '0'. Elimino ambas**

In [39]:
datos_modelo[datos_modelo['RAZA'] == '-']

COD_VERRACO CENTRO  DOSIS_REAL_x RAZA     AÑO  DOSIS_REAL_y  \
35099       2484.0    TOL          13.0    -  2019.0          88.0   

       PRODUCTIVO LINEA_GEN  CODIGO    PROCEDENCIA  
35099         1.0     TDDPP  2484.0  GRANJA ZAHARA

In [40]:
datos_modelo[datos_modelo['RAZA'] == 0].head()

COD_VERRACO CENTRO  DOSIS_REAL_x RAZA     AÑO  DOSIS_REAL_y  PRODUCTIVO  \
906       1872.0  PEÑAS          18.0    0  2015.0          61.0         0.0   
907       1872.0  PEÑAS          24.0    0  2015.0          61.0         0.0   
908       1872.0  PEÑAS          38.0    0  2015.0          61.0         0.0   
909       1872.0  PEÑAS          31.0    0  2015.0          61.0         0.0   
910       1872.0  PEÑAS          10.0    0  2015.0          61.0         0.0   

    LINEA_GEN  CODIGO  PROCEDENCIA  
906   DANBRED  1872.0  DESCONOCIDA  
907   DANBRED  1872.0  DESCONOCIDA  
908   DANBRED  1872.0  DESCONOCIDA  
909   DANBRED  1872.0  DESCONOCIDA  
910   DANBRED  1872.0  DESCONOCIDA

In [41]:
datos_modelo = datos_modelo.drop(datos_modelo[datos_modelo['RAZA'] == '-'].index, axis=0)
datos_modelo = datos_modelo.drop(datos_modelo[datos_modelo['RAZA'] == 0].index, axis=0)

In [42]:
datos_modelo['RAZA'].value_counts()

DANBRED       21051
AND            8513
PIETUPBNN      6542
PIETUPBJJ      6423
PAC            5417
TDDDD          5349
DUPIC          5152
PIETUPB        3967
TEEEE          3595
DNA            2050
PIETAXIOM      1989
DURGENES       1759
AGSG           1725
TLLLL          1635
ADN            1583
TUUUUIBE       1247
TVVVV          1173
DCAXIOM         999
LDAX            989
TPPNP           875
TPPPPTOP        871
BLUEACMC        779
TDDPP           698
LWAX            631
LDADN           548
PIETUPBFR       492
PI ALEM NP      464
TIIII           451
DCADN           428
IBERICO         396
TUUUU           294
TPPPPELI        276
LWADN           261
TZZZZGGP        236
MAXSEG          230
DURGENMJJ       223
DURGENG         222
ADNREK          221
DURGENM         205
TAAAAGGP        199
DURGENESM       165
L65P+           142
LWACMC          127
TUUUUEFI        116
TZZZZ           111
PACCAR          100
TUUUUCAL         87
PIETSERGAL       87
TUUUUGGP         30
TPPNN            22


In [43]:
datos_modelo.shape

(91159, 10)

**Eliminados los valores extraños en RAZA**

In [44]:
print(datos_modelo['DOSIS_REAL_x'].min())
print(datos_modelo['DOSIS_REAL_x'].max())

0.0
122.0


In [45]:
datos_modelo['DOSIS_REAL_x'].unique()

array([ 10.,  22.,  48.,  11.,  17.,  18.,  32.,  14.,   0.,  25.,  23.,
        21.,  33.,  58.,  15.,  43.,  12.,  13.,  70.,  24.,  28.,  36.,
        41.,  57.,  38.,  26.,  16.,  51.,  37.,   6.,  39.,  20.,   8.,
         9.,  19.,   5.,  34.,  47.,  31.,  27.,  29.,  42.,  52.,  30.,
        44.,  40.,  66.,  50.,  71.,  55.,  45.,  68.,  35.,   4.,  74.,
        59.,  53.,   3.,  67.,  80.,  61.,  64.,  54.,  63.,  90.,  62.,
        60.,  65.,  88.,  49.,  46.,   7.,   2.,  56.,  69.,  76.,  75.,
        84.,  85.,  82.,  72.,  73.,  89.,  87.,  86.,  96.,  79.,  98.,
        77.,  83.,  78.,  91.,  95.,  92.,  94., 111., 101.,  93.,  81.,
       100., 106., 103.,  97., 110., 107., 102., 109.,  99., 122., 114.,
         1.])

In [46]:
print(datos_modelo['DOSIS_REAL_y'].min())
print(datos_modelo['DOSIS_REAL_y'].max())

1.0
166.0


In [47]:
datos_modelo['DOSIS_REAL_x'].unique()

array([ 10.,  22.,  48.,  11.,  17.,  18.,  32.,  14.,   0.,  25.,  23.,
        21.,  33.,  58.,  15.,  43.,  12.,  13.,  70.,  24.,  28.,  36.,
        41.,  57.,  38.,  26.,  16.,  51.,  37.,   6.,  39.,  20.,   8.,
         9.,  19.,   5.,  34.,  47.,  31.,  27.,  29.,  42.,  52.,  30.,
        44.,  40.,  66.,  50.,  71.,  55.,  45.,  68.,  35.,   4.,  74.,
        59.,  53.,   3.,  67.,  80.,  61.,  64.,  54.,  63.,  90.,  62.,
        60.,  65.,  88.,  49.,  46.,   7.,   2.,  56.,  69.,  76.,  75.,
        84.,  85.,  82.,  72.,  73.,  89.,  87.,  86.,  96.,  79.,  98.,
        77.,  83.,  78.,  91.,  95.,  92.,  94., 111., 101.,  93.,  81.,
       100., 106., 103.,  97., 110., 107., 102., 109.,  99., 122., 114.,
         1.])

**Todo bien en DOSIS_REAL_x y DOSIS_REAL_y**

In [48]:
print(datos_modelo['AÑO'].min())
print(datos_modelo['AÑO'].max())

2016.0
2021.0


In [49]:
datos_modelo['AÑO'].unique()

array([2020., 2019., 2018., 2017., 2016., 2021.])

In [50]:
datos_modelo['PRODUCTIVO'].value_counts()

1.0    46900
0.0    44259
Name: PRODUCTIVO, dtype: int64

In [51]:
datos_modelo['PRODUCTIVO'].unique()

array([0., 1.])

**Todo OK en AÑO y PRODUCTIVO**

In [52]:
datos_modelo['LINEA_GEN'].value_counts()

DANBRED      27043
PIETUPB      17069
PAC           5517
TDDDD         5359
DUPIC         5152
TEEEE         3595
AND           3498
PTAXIOM       2576
DURGEN        2574
DNA           2224
TPPPP         2044
TUUUU         1774
TLLLL         1635
LDAX          1299
TVVVV         1173
DURAXIOM      1045
PTADN          994
BLUEACMC       779
TIIII          738
TDDPP          698
LWAX           650
AGSG           574
PTALE          464
DURADN         382
PIETUPBFR      355
TZZZZ          347
LWADN          242
LDADN          238
MAXSEG         230
ADNREK         221
TAAAA          202
L65            142
LWACMC         127
IBERICO        109
PTSER           87
PIETRAIN         3
Name: LINEA_GEN, dtype: int64

**Todo OK en cuanto a genética**

In [53]:
datos_modelo['PROCEDENCIA'].value_counts()

QUALITAT ESPERMATICA                                  6601
BURUTAIN                                              4834
DESCONOCIDA                                           3549
TAFALLA                                               3264
EXPLOTACIONES CUFA                                    2796
PEUT BV VAN DE BAARLOSEWEG 18 8316 SG MARKENSE HOL    2558
GENESUS INC OAKVILLE MB ID NO 5326121                 2338
GRUPO ALTOPASO A CORUÑA                               2112
CAN JAUMO                                             1883
ESCORIAL                                              1838
LA COMETA                                             1747
AIM LEON                                              1688
DESCONOCIDO                                           1683
ZAHARA                                                1669
FUGLSANG DENMARK 4160 HERLUFMAGLE                     1660
NAVARRA                                               1525
MAS GALLAT                                            15

**Se puede apreciar tres procedencias iguales con distinto nombre: DESCONOCIDO, DESCONOCIDA, DECONOCIDA**

In [54]:
datos_modelo[datos_modelo['PROCEDENCIA'] == 'DESCONOCIDO'].head()

COD_VERRACO CENTRO  DOSIS_REAL_x     RAZA     AÑO  DOSIS_REAL_y  \
4202       2326.0    CAL          26.0  DANBRED  2020.0          58.0   
4203       2326.0    CAL          16.0  DANBRED  2020.0          58.0   
4204       2326.0    CAL          20.0  DANBRED  2020.0          58.0   
4205       2326.0    CAL          27.0  DANBRED  2020.0          58.0   
4206       2326.0    CAL          28.0  DANBRED  2020.0          58.0   

      PRODUCTIVO LINEA_GEN  CODIGO  PROCEDENCIA  
4202         0.0   DANBRED  2326.0  DESCONOCIDO  
4203         0.0   DANBRED  2326.0  DESCONOCIDO  
4204         0.0   DANBRED  2326.0  DESCONOCIDO  
4205         0.0   DANBRED  2326.0  DESCONOCIDO  
4206         0.0   DANBRED  2326.0  DESCONOCIDO

In [55]:
datos_modelo[datos_modelo['PROCEDENCIA'] == 'DESCONOCIDA'].head()

COD_VERRACO CENTRO  DOSIS_REAL_x     RAZA     AÑO  DOSIS_REAL_y  \
433       1872.0    CAL           9.0  DANBRED  2020.0          11.0   
434       1872.0    CAL          31.0  DANBRED  2020.0          11.0   
435       1872.0    CAL           4.0  DANBRED  2020.0          11.0   
436       1872.0    CAL          26.0  DANBRED  2020.0          11.0   
437       1872.0    CAL          19.0  DANBRED  2020.0          11.0   

     PRODUCTIVO LINEA_GEN  CODIGO  PROCEDENCIA  
433         0.0   DANBRED  1872.0  DESCONOCIDA  
434         0.0   DANBRED  1872.0  DESCONOCIDA  
435         0.0   DANBRED  1872.0  DESCONOCIDA  
436         0.0   DANBRED  1872.0  DESCONOCIDA  
437         0.0   DANBRED  1872.0  DESCONOCIDA

In [56]:
datos_modelo[datos_modelo['PROCEDENCIA'] == 'DECONOCIDO'].head()

COD_VERRACO CENTRO  DOSIS_REAL_x     RAZA     AÑO  DOSIS_REAL_y  \
12927       2421.0  PEÑAS          21.0  DANBRED  2020.0          30.0   
12928       2421.0  PEÑAS          30.0  DANBRED  2020.0          30.0   
12929       2421.0  PEÑAS          16.0  DANBRED  2020.0          30.0   
12930       2421.0  PEÑAS          21.0  DANBRED  2020.0          30.0   
12931       2421.0  PEÑAS          25.0  DANBRED  2020.0          30.0   

       PRODUCTIVO LINEA_GEN  CODIGO PROCEDENCIA  
12927         0.0   DANBRED  2421.0  DECONOCIDO  
12928         0.0   DANBRED  2421.0  DECONOCIDO  
12929         0.0   DANBRED  2421.0  DECONOCIDO  
12930         0.0   DANBRED  2421.0  DECONOCIDO  
12931         0.0   DANBRED  2421.0  DECONOCIDO

In [57]:
datos_modelo['PROCEDENCIA'] = np.where(datos_modelo['PROCEDENCIA'] == 'DESCONOCIDO', datos_modelo['PROCEDENCIA'] == 'DESCONOCIDA', datos_modelo['PROCEDENCIA'])
datos_modelo['PROCEDENCIA'] = np.where(datos_modelo['PROCEDENCIA'] == 'DECONOCIDO', datos_modelo['PROCEDENCIA'] == 'DESCONOCIDA', datos_modelo['PROCEDENCIA'])

In [58]:
datos_modelo['PROCEDENCIA'].value_counts()

QUALITAT ESPERMATICA                                  6601
BURUTAIN                                              4834
DESCONOCIDA                                           3549
TAFALLA                                               3264
EXPLOTACIONES CUFA                                    2796
PEUT BV VAN DE BAARLOSEWEG 18 8316 SG MARKENSE HOL    2558
GENESUS INC OAKVILLE MB ID NO 5326121                 2338
GRUPO ALTOPASO A CORUÑA                               2112
False                                                 1887
CAN JAUMO                                             1883
ESCORIAL                                              1838
LA COMETA                                             1747
AIM LEON                                              1688
ZAHARA                                                1669
FUGLSANG DENMARK 4160 HERLUFMAGLE                     1660
NAVARRA                                               1525
MAS GALLAT                                            15

# FEATURE ENGINEERING

In [59]:
datos_modelo.head()

COD_VERRACO CENTRO  DOSIS_REAL_x     RAZA     AÑO  DOSIS_REAL_y  \
0       2095.0    CAL          10.0  DANBRED  2020.0          18.0   
1       2095.0    CAL          22.0  DANBRED  2020.0          18.0   
2       2095.0    CAL          48.0  DANBRED  2020.0          18.0   
3       2095.0    CAL          11.0  DANBRED  2020.0          18.0   
4       2095.0    CAL          17.0  DANBRED  2020.0          18.0   

   PRODUCTIVO LINEA_GEN  CODIGO                        PROCEDENCIA  
0         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE  
1         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE  
2         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE  
3         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE  
4         0.0   DANBRED  2095.0  FUGLSANG DENMARK 4160 HERLUFMAGLE

In [60]:
datos_modelo.shape

(91159, 10)

**CENTRO, RAZA, LINEA_GEN y PROCEDENCIA son variables categóricas las cuales han de ser codificadas para poder introducirlas como parámetros al modelo. Para ello, utilizaré la técninca de Target Encoding**

**¡Importante!: Target Encoding se realiza solo sobre el conjunto de train. El algoritmo tiene que ser capaz de, cuando se le pase una lista de razas, identificarlas, asignarle probabilidades y calcular su influencia en la productividad. Al algoritmo no se le va a introducir las razas ya codificadas, sino una lista con las diferentes razas nuevas existentes.**

In [61]:
train, test = train_test_split(datos_modelo)

In [62]:
train.shape, test.shape

((68369, 10), (22790, 10))

In [63]:
datos_modelo['RAZA'].value_counts()

DANBRED       21051
AND            8513
PIETUPBNN      6542
PIETUPBJJ      6423
PAC            5417
TDDDD          5349
DUPIC          5152
PIETUPB        3967
TEEEE          3595
DNA            2050
PIETAXIOM      1989
DURGENES       1759
AGSG           1725
TLLLL          1635
ADN            1583
TUUUUIBE       1247
TVVVV          1173
DCAXIOM         999
LDAX            989
TPPNP           875
TPPPPTOP        871
BLUEACMC        779
TDDPP           698
LWAX            631
LDADN           548
PIETUPBFR       492
PI ALEM NP      464
TIIII           451
DCADN           428
IBERICO         396
TUUUU           294
TPPPPELI        276
LWADN           261
TZZZZGGP        236
MAXSEG          230
DURGENMJJ       223
DURGENG         222
ADNREK          221
DURGENM         205
TAAAAGGP        199
DURGENESM       165
L65P+           142
LWACMC          127
TUUUUEFI        116
TZZZZ           111
PACCAR          100
TUUUUCAL         87
PIETSERGAL       87
TUUUUGGP         30
TPPNN            22


**Como se puede apreciar en la lista arriba mostrada, de las razas TAAAA y DAN-INGA solo existen 3 y 1 verracos respectivamente. Las conclusiones que se obtengan en base a la probabilidad de ser productivo en base a esas determinadas razas no van a ser muy fiables**

In [64]:
razas_encoded = train.groupby('RAZA')['PRODUCTIVO'].agg(['mean', 'count']).sort_values(by='count', ascending=False)
razas_encoded

mean  count
RAZA                       
DANBRED     0.712503  15708
AND         0.720894   6399
PIETUPBNN   0.337934   4927
PIETUPBJJ   0.600370   4862
PAC         0.243902   4100
TDDDD       0.431056   4025
DUPIC       0.558793   3878
PIETUPB     0.531532   2997
TEEEE       0.380023   2663
DNA         0.850804   1555
PIETAXIOM   0.354405   1487
DURGENES    0.251926   1298
AGSG        0.580620   1290
TLLLL       0.672330   1236
ADN         0.385345   1160
TUUUUIBE    0.325134    935
TVVVV       0.304248    871
LDAX        0.158455    751
DCAXIOM     0.644000    750
TPPNP       0.316770    644
TPPPPTOP    0.332293    641
BLUEACMC    0.102740    584
TDDPP       0.398131    535
LWAX        0.450000    460
LDADN       0.419048    420
PIETUPBFR   0.000000    369
PI ALEM NP  0.000000    359
TIIII       0.000000    319
DCADN       0.630225    311
IBERICO     0.288079    302
TUUUU       0.607477    214
TPPPPELI    0.345972    211
LWADN       0.320197    203
TZZZZGGP    0.000000    177
MAXSEG      0.724551    167
DURGENG     0.000000    167
DURGENMJJ   0.132911    158
DURGENM     0.297468    158
ADNREK      0.000000    156
TAAAAGGP    0.000000    152
DURGENESM   0.000000    122
L65P+       0.000000    117
LWACMC      0.000000     95
TUUUUEFI    0.000000     89
TZZZZ       0.000000     81
PACCAR      0.000000     76
PIETSERGAL  0.000000     69
TUUUUCAL    0.893939     66
TUUUUGGP    0.000000     27
TPPNN       0.000000     16
TDDDDTOP    0.000000      8
TAAAA       0.000000      3
DAN-INGA    1.000000      1

**COMENTARIO RAZAS**

In [65]:
razas_encoded = train.groupby('RAZA')['PRODUCTIVO'].mean()
razas_encoded = pd.DataFrame(razas_encoded)
razas_encoded.columns = ['RAZA_ENCODED']
razas_encoded.head()

RAZA_ENCODED
RAZA                  
ADN           0.385345
ADNREK        0.000000
AGSG          0.580620
AND           0.720894
BLUEACMC      0.102740

In [66]:
centros_encoded = train.groupby(['CENTRO'])['PRODUCTIVO'].agg(['mean', 'count']).sort_values(by='count', ascending=False)
centros_encoded

mean  count
CENTRO                 
CAL     0.419520  41147
PEÑAS   0.690852  24781
TOL     0.312167   2441

In [67]:
centros_encoded = train.groupby(['CENTRO'])['PRODUCTIVO'].mean()
centros_encoded = pd.DataFrame(centros_encoded)
centros_encoded = centros_encoded.rename(columns = {'PRODUCTIVO':'CENTRO_ENCODED'})
centros_encoded

CENTRO_ENCODED
CENTRO                
CAL           0.419520
PEÑAS         0.690852
TOL           0.312167

In [68]:
genetica_encoded = train.groupby(['LINEA_GEN'])['PRODUCTIVO'].agg(['mean', 'count']).sort_values(by='count', ascending=False)
genetica_encoded

mean  count
LINEA_GEN                 
DANBRED    0.718526  20215
PIETUPB    0.478874  12899
PAC        0.239464   4176
TDDDD      0.430201   4033
DUPIC      0.558793   3878
TEEEE      0.380023   2663
AND        0.623139   2619
PTAXIOM    0.422037   1924
DURGEN     0.207567   1903
DNA        0.850473   1692
TPPPP      0.324074   1512
TUUUU      0.370398   1331
TLLLL      0.672330   1236
LDAX       0.298281    989
TVVVV      0.304248    871
DURAXIOM   0.633333    780
PTADN      0.224688    721
BLUEACMC   0.102740    584
TDDPP      0.398131    535
TIIII      0.163227    533
LWAX       0.434874    476
AGSG       0.661972    426
PTALE      0.000000    359
DURADN     0.658363    281
TZZZZ      0.000000    258
PIETUPBFR  0.000000    256
LWADN      0.347594    187
LDADN      0.000000    182
MAXSEG     0.724551    167
ADNREK     0.000000    156
TAAAA      0.000000    155
L65        0.000000    117
LWACMC     0.000000     95
IBERICO    0.000000     88
PTSER      0.000000     69
PIETRAIN   0.000000      3

In [69]:
genetica_encoded = train.groupby(['LINEA_GEN'])['PRODUCTIVO'].mean()
genetica_encoded = pd.DataFrame(genetica_encoded)
genetica_encoded = genetica_encoded.rename(columns = {'PRODUCTIVO':'GENETICA_ENCODED'})
genetica_encoded

GENETICA_ENCODED
LINEA_GEN                  
ADNREK             0.000000
AGSG               0.661972
AND                0.623139
BLUEACMC           0.102740
DANBRED            0.718526
DNA                0.850473
DUPIC              0.558793
DURADN             0.658363
DURAXIOM           0.633333
DURGEN             0.207567
IBERICO            0.000000
L65                0.000000
LDADN              0.000000
LDAX               0.298281
LWACMC             0.000000
LWADN              0.347594
LWAX               0.434874
MAXSEG             0.724551
PAC                0.239464
PIETRAIN           0.000000
PIETUPB            0.478874
PIETUPBFR          0.000000
PTADN              0.224688
PTALE              0.000000
PTAXIOM            0.422037
PTSER              0.000000
TAAAA              0.000000
TDDDD              0.430201
TDDPP              0.398131
TEEEE              0.380023
TIIII              0.163227
TLLLL              0.672330
TPPPP              0.324074
TUUUU              0.370398
TVVVV              0.304248
TZZZZ              0.000000

In [70]:
procedencia_encoded = train.groupby(['PROCEDENCIA'])['PRODUCTIVO'].agg(['mean', 'count']).sort_values(by='count', ascending=False)
procedencia_encoded

mean  count
PROCEDENCIA                                                        
QUALITAT ESPERMATICA                                0.773627   4952
BURUTAIN                                            0.386039   3567
DESCONOCIDA                                         0.651664   2644
TAFALLA                                             0.650735   2448
EXPLOTACIONES CUFA                                  0.730332   2110
PEUT BV VAN DE BAARLOSEWEG 18 8316 SG MARKENSE HOL  0.497122   1911
GENESUS INC OAKVILLE MB ID NO 5326121               0.229919   1718
GRUPO ALTOPASO A CORUÑA                             0.724355   1589
False                                               0.736287   1422
CAN JAUMO                                           0.579690   1418
ESCORIAL                                            0.470238   1344
LA COMETA                                           0.430294   1327
FUGLSANG DENMARK 4160 HERLUFMAGLE                   0.824000   1250
AIM LEON                                            0.233923   1244
ZAHARA                                              0.237288   1239
MAS GALLAT                                          0.498279   1162
NAVARRA                                             0.809811   1162
USA                                                 0.858896   1141
FINA MARKUS AM LAUBENBUCH 2 ALEMANIA                0.410065   1073
LA MASIA                                            0.756808   1065
HASTRUPGARD HASTRUPGARDSVEJ 8 7000 FREDERICIA DK    0.643979    955
NEHER STEPHAN DORFSTR 16 ALEMANIA                   0.621019    942
PEÑAS DE SAN PEDRO                                  0.399103    892
LIPPERT NORBERT AURAER STR 1 ALEMANIA               0.730769    884
UPB GENETIC                                         0.454545    880
QUALITAT                                            0.534264    788
SCHWARZ WOLFGANG BACHT STR 14 ALEMANIA              0.464239    769
GRUPO ALTOPASO A CORUÑA ES150800089301              0.574380    726
EL ESCORIAL                                         0.490085    706
BUJARALOZ                                           0.513043    690
VOLSGAARD I DAMSTRUPVEJ 2 6973 OHRNOJ  DENMARK      0.997050    678
COMETA                                              0.465875    674
MAALING AVL OG OPFORMERING SKELDEMARG 10 DENMARK    0.691574    629
KERNEIS KERINOU LE CONQUET 29217 FRANCIA            0.751227    611
ELTZABURU                                           0.102740    584
ACOMPOR                                             0.350970    567
GRANJA ZAHARA                                       0.613309    556
KUGEL GEORG MAUERNER STR 23A ALEMANIA               0.000000    553
ECKARDT BERND GBR HOHNWEG 14 ALEMANIA               0.616236    542
MUNKBRO II MUNKBROVEJ 7 7500 HOLSTEBRO DENMARK      0.884972    539
HASTRUPGARD, HASTRUPGARDSVEJ 7000 FREDERICIA DENMA  0.000000    527
AVLSCENTRET HOLMEGARD A/S, FALDSLEDVEJ FABORG DK    0.998058    515
AIM ANDALUCIA                                       0.377470    506
TOJAPIGS SARL DROMBAS DROMBAS FRANCE                0.602767    506
ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA     0.374000    500
AIM PEÑAS                                           0.630197    457
VAN DE PEUT B.V.                                    0.502283    438
LYKKENSGAARD AVLSCENTER ELLEDEVEJ 95 DENMARK        0.951945    437
NAVALAGAMELLA                                       0.436490    433
TOJAPIGS SARL DOMBRAS-1, RUE NAPOLEON FRANCIA       0.311905    420
GRANJA ZAHARA TOLEDO ESPAÑA                         0.141148    418
ROHWER JURGEN BOKELER STR 5 24793 BRAMMER ALEMANIA  0.457002    407
SCWARZ WOLFGANG BACHSTR 14 SALCHING ALEMANIA        0.000000    397
TOM RATHJE COLUMBUS NEBRASKA USA                    0.966752    391
ELEVAGE DE BIZY OUZOUER LE MARCHE 41240 FRANCIA     0.943700    373
SINOVAS                                             0.497253    364
ALBAGES                                             0.403361    357
AIM ANDALUCÍA                               

In [71]:
procedencia_encoded = train.groupby(['PROCEDENCIA'])['PRODUCTIVO'].mean()
procedencia_encoded = pd.DataFrame(procedencia_encoded)
procedencia_encoded = procedencia_encoded.rename(columns = {'PRODUCTIVO':'PROCEDENCIA_ENCODED'})
procedencia_encoded

PROCEDENCIA_ENCODED
PROCEDENCIA                                                            
False                                                          0.736287
ACOMPOR                                                        0.350970
AGER                                                           0.419753
AIM ANDALUCIA                                                  0.377470
AIM ANDALUCÍA                                                  0.571831
AIM CENTRO                                                     0.000000
AIM LEON                                                       0.233923
AIM PEÑAS                                                      0.630197
AIM SINOVAS                                                    0.000000
AIM SORIA                                                      0.000000
ALBAGES                                                        0.403361
ALMOLDA                                                        0.000000
ALMUDEVAR                                                      0.000000
ARANDA DE DUERO                                                0.523810
ATEZ                                                           0.000000
ATEZ (NAVARRA)                                                 0.000000
AVLSCENTRET HOLMEGARD A/S, FALDSLEDVEJ FABORG DK               0.998058
BARCELONA                                                      0.000000
BERGSHOLM VIDAR N 3160 STOKKE NORUEGA                          0.000000
BERGSHOLM VIDAR N-3160 STOKKE NORUEGA                          0.515625
BEUNZA                                                         0.333333
BIURRUN                                                        0.000000
BUJARALOZ                                                      0.513043
BURUTAIN                                                       0.386039
CAN CARRERAS                                                   0.000000
CAN JAUMO                                                      0.579690
CASETA SANTASUSANA SAN MATEU DE BAGES                          0.000000
CHANTELOUP                                                     0.000000
COMETA                                                         0.465875
DESCONOCIDA                                                    0.651664
EARL ARMANE LE BOIS CLAIR EVAILLE 72120 FRANCIA                0.000000
EARL DARTOIS BEAUCHENE GUITE FRANCE                            0.000000
EARL FERME DE LA VALLE 650 RUE DU PIRE ALLER FRANC             0.539683
EARL FERME DE LA VALLEE HERBINGHEM FRANCE                      0.000000
ECKARDT BEECKARDT BERND SONNEFELD GERMANY                      0.000000
ECKARDT BERND GBR HOHNWEG 14 ALEMANIA                          0.616236
ECKARDT BERND HOHNWEG 14 SONNFELD GERMANY                      0.000000
ECKARDT BERND SONNEFELD GERMANY                                0.000000
EL ESCORIAL                                                    0.490085
ELEVAGE DE BIZY OUZOUER LE MARCHE 41240 FRANCIA                0.943700
ELEVAGE DE BIZY OUZOUER LE MARCHE FRANCE                       0.000000
ELEVAGE DE BIZY OUZOUERLE MARCHE FRANCE                        0.000000
ELTZABURU                                                      0.102740
ERTL JOHANNES FRAUNBERG GERMANY                                0.000000
ERTL JOHANNES GROSSHUNDLBACH 12 ALEMANIA                       0.361111
ES5010370130002-00864                                          0.000000
ESCORIAL                                                       0.470238
ESKEGAARD A/S MOLLEGYDE HADERSLEV DENMARK                      0.000000
EXPLOTACIONES CUFA                                             0.730332
EXPLOTACIONES CUFA SL                                          0.000000
EXPLTACIONES CUFA                                              0.836066
FINA MARKUS AM LAUBENBUCH 2 ALEMANIA                           0.410065
FINA MARKUS AM LAUBENBUCH 2 WEIBENBURG ALEMANIA                0.000000
FINA MARKUS AM LAUBENBUCH WEIBENBURG ALEMANIA                  0.000000
FINA MARKUS AM LAUBE

In [72]:
train = train.merge(razas_encoded, how='outer', left_on='RAZA', right_index=True)

In [73]:
train = train.merge(centros_encoded, how='outer', left_on='CENTRO', right_index=True)

In [74]:
train = train.merge(genetica_encoded, how='outer', left_on='LINEA_GEN', right_index=True)

In [75]:
train = train.merge(procedencia_encoded, how='outer', left_on='PROCEDENCIA', right_index=True)

In [76]:
train.head()

COD_VERRACO CENTRO  DOSIS_REAL_x       RAZA     AÑO  DOSIS_REAL_y  \
9104       2601.0    CAL           0.0  PIETUPBNN  2020.0          80.0   
8651       2585.0    CAL          10.0  PIETUPBNN  2020.0          62.0   
8669       2585.0    CAL          12.0  PIETUPBNN  2020.0          62.0   
8614       2583.0    CAL          19.0  PIETUPBNN  2020.0          70.0   
8663       2585.0    CAL          12.0  PIETUPBNN  2020.0          62.0   

      PRODUCTIVO LINEA_GEN  CODIGO  \
9104         1.0   PIETUPB  2601.0   
8651         0.0   PIETUPB  2585.0   
8669         0.0   PIETUPB  2585.0   
8614         0.0   PIETUPB  2583.0   
8663         0.0   PIETUPB  2585.0   

                                          PROCEDENCIA  RAZA_ENCODED  \
9104  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8651  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8669  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8614  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8663  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   

      CENTRO_ENCODED  GENETICA_ENCODED  PROCEDENCIA_ENCODED  
9104         0.41952          0.478874                0.374  
8651         0.41952          0.478874                0.374  
8669         0.41952          0.478874                0.374  
8614         0.41952          0.478874                0.374  
8663         0.41952          0.478874                0.374

In [77]:
train['PROCEDENCIA_ENCODED'].unique()

array([0.374     , 0.62101911, 0.45700246, 0.46423927, 0.41006524,
       0.36111111, 0.73076923, 0.4302939 , 0.        , 0.5796897 ,
       0.80981067, 0.61623616, 0.35097002, 0.39910314, 0.75680751,
       0.45454545, 0.46587537, 0.76785714, 0.41975309, 0.10273973,
       0.51304348, 0.4702381 , 0.65073529, 0.38603869, 0.65166415,
       0.77362682, 0.73628692, 0.824     , 0.64478764, 0.63019694,
       0.83606557, 0.53426396, 0.64397906, 0.99805825, 0.73033175,
       0.86315789, 0.95194508, 0.69157393, 0.99705015, 0.88497217,
       0.94230769, 0.40336134, 0.33333333, 0.28571429, 0.49827883,
       0.22991851, 0.37747036, 0.85889571, 0.96675192, 0.23392283,
       0.515625  , 0.57438017, 0.21575342, 0.72435494, 0.57183099,
       0.50228311, 0.49712193, 0.49844237, 0.31190476, 0.6027668 ,
       0.45962733, 0.49008499, 0.49725275, 0.7512275 , 0.53968254,
       0.64220183, 0.23049645, 0.14114833, 0.64347826, 0.43648961,
       0.52380952, 0.61389961, 0.94369973, 0.49006623, 0.81428

**Ya tengo las variables categóricas codificadas con valores numéricos**

**Los valores de las variables categóricas estan en tanto por 1. He de escalar el valor de DOSIS_REAL_x (dosis reales en cada extracción) para poder compararlas**

In [78]:
train['DOSIS_REAL_x'].head()

9104     0.0
8651    10.0
8669    12.0
8614    19.0
8663    12.0
Name: DOSIS_REAL_x, dtype: float64

In [79]:
#normalizado = (train['DOSIS_REAL_x'] - min(train['DOSIS_REAL_x']))/(max(train['DOSIS_REAL_x'])-min(train['DOSIS_REAL_x']))

In [80]:
#normalizado.min()

In [81]:
#normalizado.max()

In [82]:
#train['DOSIS_REAL_x_NORMALIZADO'] = normalizado

In [83]:
#train['DOSIS_REAL_x_NORMALIZADO'].head()

In [84]:
train.head()

COD_VERRACO CENTRO  DOSIS_REAL_x       RAZA     AÑO  DOSIS_REAL_y  \
9104       2601.0    CAL           0.0  PIETUPBNN  2020.0          80.0   
8651       2585.0    CAL          10.0  PIETUPBNN  2020.0          62.0   
8669       2585.0    CAL          12.0  PIETUPBNN  2020.0          62.0   
8614       2583.0    CAL          19.0  PIETUPBNN  2020.0          70.0   
8663       2585.0    CAL          12.0  PIETUPBNN  2020.0          62.0   

      PRODUCTIVO LINEA_GEN  CODIGO  \
9104         1.0   PIETUPB  2601.0   
8651         0.0   PIETUPB  2585.0   
8669         0.0   PIETUPB  2585.0   
8614         0.0   PIETUPB  2583.0   
8663         0.0   PIETUPB  2585.0   

                                          PROCEDENCIA  RAZA_ENCODED  \
9104  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8651  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8669  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8614  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8663  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   

      CENTRO_ENCODED  GENETICA_ENCODED  PROCEDENCIA_ENCODED  
9104         0.41952          0.478874                0.374  
8651         0.41952          0.478874                0.374  
8669         0.41952          0.478874                0.374  
8614         0.41952          0.478874                0.374  
8663         0.41952          0.478874                0.374

**Ya tengo las cuatro variables codificadas en tanto por 1, listas para ser modeladas**

# CREACIÓN DEL MODELO

In [85]:
train['PROCEDENCIA']

9104        ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
8651        ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
8669        ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
8614        ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
8663        ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
8808        ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
9978        ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
36027       ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
36046       ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
9146        ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
36002       ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
36023       ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
36018       ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
8645        ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
35971       ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
9661        ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA
9653        ROHWER TIMO LOOPER WEG 19 24

In [86]:
train['PROCEDENCIA_ENCODED'].isna().value_counts()

False    68369
Name: PROCEDENCIA_ENCODED, dtype: int64

In [87]:
jesus = train.loc[:, 'PROCEDENCIA_ENCODED']

In [88]:
jesus.isna().value_counts()

False    68369
Name: PROCEDENCIA_ENCODED, dtype: int64

In [89]:
type(train.loc[:, ['RAZA_ENCODED', 'CENTRO_ENCODED', 'GENETICA_ENCODED', 'PROCEDECNIA_ENCODED', 'DOSIS_REAL_x', 'DOSIS_REAL_y']])

/home/dsc/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)


pandas.core.frame.DataFrame

In [90]:
train.head()

COD_VERRACO CENTRO  DOSIS_REAL_x       RAZA     AÑO  DOSIS_REAL_y  \
9104       2601.0    CAL           0.0  PIETUPBNN  2020.0          80.0   
8651       2585.0    CAL          10.0  PIETUPBNN  2020.0          62.0   
8669       2585.0    CAL          12.0  PIETUPBNN  2020.0          62.0   
8614       2583.0    CAL          19.0  PIETUPBNN  2020.0          70.0   
8663       2585.0    CAL          12.0  PIETUPBNN  2020.0          62.0   

      PRODUCTIVO LINEA_GEN  CODIGO  \
9104         1.0   PIETUPB  2601.0   
8651         0.0   PIETUPB  2585.0   
8669         0.0   PIETUPB  2585.0   
8614         0.0   PIETUPB  2583.0   
8663         0.0   PIETUPB  2585.0   

                                          PROCEDENCIA  RAZA_ENCODED  \
9104  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8651  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8669  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8614  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8663  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   

      CENTRO_ENCODED  GENETICA_ENCODED  PROCEDENCIA_ENCODED  
9104         0.41952          0.478874                0.374  
8651         0.41952          0.478874                0.374  
8669         0.41952          0.478874                0.374  
8614         0.41952          0.478874                0.374  
8663         0.41952          0.478874                0.374

In [91]:
x_train = train.loc[:, ['RAZA_ENCODED', 'CENTRO_ENCODED', 'GENETICA_ENCODED', 'PROCEDENCIA_ENCODED', 'DOSIS_REAL_x', 'DOSIS_REAL_y']]
y_train = train['PRODUCTIVO']

In [92]:
test.head()

COD_VERRACO CENTRO  DOSIS_REAL_x      RAZA     AÑO  DOSIS_REAL_y  \
7655         2459.0    CAL          17.0   PIETUPB  2019.0          95.0   
120529       2010.0    CAL           0.0  TUUUUIBE  2016.0          74.0   
44467        2242.0    CAL          16.0     DUPIC  2017.0          45.0   
12888        2568.0  PEÑAS          19.0   DANBRED  2020.0         136.0   
110107       1617.0    CAL          26.0       PAC  2016.0          84.0   

        PRODUCTIVO LINEA_GEN  CODIGO  \
7655           1.0   PIETUPB  2459.0   
120529         0.0     TUUUU  2010.0   
44467          0.0     DUPIC  2242.0   
12888          1.0   DANBRED  2568.0   
110107         1.0       PAC  1617.0   

                                             PROCEDENCIA  
7655               ECKARDT BERND GBR HOHNWEG 14 ALEMANIA  
120529                                          ESCORIAL  
44467                                            TAFALLA  
12888   HASTRUPGARD HASTRUPGARDSVEJ 8 7000 FREDERICIA DK  
110107                                PEÑAS DE SAN PEDRO

In [93]:
test = test.merge(razas_encoded, how='outer', left_on='RAZA', right_index=True)

test = test.merge(centros_encoded, how='outer', left_on='CENTRO', right_index=True)

test = test.merge(genetica_encoded, how='outer', left_on='LINEA_GEN', right_index=True)

test = test.merge(procedencia_encoded, how='outer', left_on='PROCEDENCIA', right_index=True)

#normalizado = (test['DOSIS_REAL_x'] - min(test['DOSIS_REAL_x']))/(max(test['DOSIS_REAL_x'])-min(test['DOSIS_REAL_x']))
#test['DOSIS_REAL_x_NORMALIZADO'] = normalizado

In [94]:
test.head()

COD_VERRACO CENTRO  DOSIS_REAL_x     RAZA     AÑO  DOSIS_REAL_y  \
7655       2459.0    CAL          17.0  PIETUPB  2019.0          95.0   
7615       2459.0    CAL           0.0  PIETUPB  2020.0          56.0   
8877       2461.0    CAL          14.0  PIETUPB  2020.0          92.0   
3991       2460.0    CAL          18.0  PIETUPB  2019.0          86.0   
9015       2461.0    CAL          21.0  PIETUPB  2019.0          87.0   

      PRODUCTIVO LINEA_GEN  CODIGO                            PROCEDENCIA  \
7655         1.0   PIETUPB  2459.0  ECKARDT BERND GBR HOHNWEG 14 ALEMANIA   
7615         0.0   PIETUPB  2459.0  ECKARDT BERND GBR HOHNWEG 14 ALEMANIA   
8877         1.0   PIETUPB  2461.0  ECKARDT BERND GBR HOHNWEG 14 ALEMANIA   
3991         1.0   PIETUPB  2460.0  ECKARDT BERND GBR HOHNWEG 14 ALEMANIA   
9015         1.0   PIETUPB  2461.0  ECKARDT BERND GBR HOHNWEG 14 ALEMANIA   

      RAZA_ENCODED  CENTRO_ENCODED  GENETICA_ENCODED  PROCEDENCIA_ENCODED  
7655      0.531532         0.41952          0.478874             0.616236  
7615      0.531532         0.41952          0.478874             0.616236  
8877      0.531532         0.41952          0.478874             0.616236  
3991      0.531532         0.41952          0.478874             0.616236  
9015      0.531532         0.41952          0.478874             0.616236

In [95]:
x_test = test.loc[:, ['RAZA_ENCODED', 'CENTRO_ENCODED', 'GENETICA_ENCODED', 'PROCEDENCIA_ENCODED', 'DOSIS_REAL_x', 'DOSIS_REAL_y']]
y_test = test['PRODUCTIVO']

**Redondeo los decimales de los float a 3 puesto que a veces el clasificador me daba problemas por la longitud de estos mismos**

In [96]:
type(x_test)

pandas.core.frame.DataFrame

In [97]:
type(x_train)

pandas.core.frame.DataFrame

In [98]:
x_train.head()

RAZA_ENCODED  CENTRO_ENCODED  GENETICA_ENCODED  PROCEDENCIA_ENCODED  \
9104      0.337934         0.41952          0.478874                0.374   
8651      0.337934         0.41952          0.478874                0.374   
8669      0.337934         0.41952          0.478874                0.374   
8614      0.337934         0.41952          0.478874                0.374   
8663      0.337934         0.41952          0.478874                0.374   

      DOSIS_REAL_x  DOSIS_REAL_y  
9104           0.0          80.0  
8651          10.0          62.0  
8669          12.0          62.0  
8614          19.0          70.0  
8663          12.0          62.0

In [99]:
train.head()

COD_VERRACO CENTRO  DOSIS_REAL_x       RAZA     AÑO  DOSIS_REAL_y  \
9104       2601.0    CAL           0.0  PIETUPBNN  2020.0          80.0   
8651       2585.0    CAL          10.0  PIETUPBNN  2020.0          62.0   
8669       2585.0    CAL          12.0  PIETUPBNN  2020.0          62.0   
8614       2583.0    CAL          19.0  PIETUPBNN  2020.0          70.0   
8663       2585.0    CAL          12.0  PIETUPBNN  2020.0          62.0   

      PRODUCTIVO LINEA_GEN  CODIGO  \
9104         1.0   PIETUPB  2601.0   
8651         0.0   PIETUPB  2585.0   
8669         0.0   PIETUPB  2585.0   
8614         0.0   PIETUPB  2583.0   
8663         0.0   PIETUPB  2585.0   

                                          PROCEDENCIA  RAZA_ENCODED  \
9104  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8651  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8669  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8614  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   
8663  ROHWER TIMO LOOPER WEG 19 24589 SCHULP ALEMANIA      0.337934   

      CENTRO_ENCODED  GENETICA_ENCODED  PROCEDENCIA_ENCODED  
9104         0.41952          0.478874                0.374  
8651         0.41952          0.478874                0.374  
8669         0.41952          0.478874                0.374  
8614         0.41952          0.478874                0.374  
8663         0.41952          0.478874                0.374

In [100]:
jesus.head()

9104    0.374
8651    0.374
8669    0.374
8614    0.374
8663    0.374
Name: PROCEDENCIA_ENCODED, dtype: float64